## Packages

In [2]:
!pip install earthengine-api
!pip install ee
!pip install geemap
!pip install retry

!pip install ipyleaflet

In [3]:
# Geo work
import ee
import geemap.geemap as geemap
import geopandas as gpd
from shapely.geometry import Polygon, mapping
import json


# Data processing
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
import os

# Visualization
#import matplotlib as plt
import ipyleaflet
from ipyleaflet import *
from bqplot import pyplot as plt

#Multiprocessing
import logging
import multiprocessing
import requests
import shutil
from retry import retry

ModuleNotFoundError: No module named 'StringIO'

## GEE service account

In [3]:
service_account = 'project-lc@lewagon-lc-amelietatin.iam.gserviceaccount.com'

In [4]:
credentials = ee.ServiceAccountCredentials(service_account, './key.json')

In [5]:
ee.Initialize(credentials)

## Open protected areas

In [41]:
shapefile = ee.FeatureCollection("projects/lewagon-lc-amelietatin/assets/sample_filtered_protected_areas_10")

In [42]:
shapefile

In [43]:
pwd

'/Users/amelietatin/code/amelietatin/Predicting_land_cover/notebooks'

In [44]:
pa_sample = gpd.read_file("../raw_data/sample_protected_areas/sample_filtered_protected_areas_10/sample_filtered_protected_areas_10.shp")

In [9]:
pa_sample.head(2)

SITECODE               SITENAME        lon        lat  \
0  IT7222296   Sella di Vinchiaturo  14.594088  41.454862   
1  SE0630108  Stensjön och Lomtjärn  16.256044  62.138628   

                                            geometry  
0  POLYGON ((4704636.130 2052459.208, 4704645.330...  
1  POLYGON ((4648648.630 4353662.162, 4648694.418...

In [10]:
#Define which sitecode to show on the map
sitecodes = pa_sample['SITECODE']
pa_sitecode = sitecodes[6]
pa_sitecode

'BG0000273'

In [31]:
gpd.GeoDataFrame(pa_sample.iloc[0]).T

SITECODE              SITENAME        lon        lat  \
0  IT7222296  Sella di Vinchiaturo  14.594088  41.454862   

                                            geometry  
0  POLYGON ((4704636.130 2052459.208, 4704645.330...

In [25]:
type(pd.DataFrame(pa_sample.iloc[0]).T)

pandas.core.frame.DataFrame

In [36]:
pa_sample.iloc[[0]]

SITECODE              SITENAME        lon        lat  \
0  IT7222296  Sella di Vinchiaturo  14.594088  41.454862   

                                            geometry  
0  POLYGON ((4704636.130 2052459.208, 4704645.330...

## Select quartal

In [11]:
# Specify the start and end dates
start_date = datetime(2015, 7, 1)
end_date = datetime(2024, 4, 30)

# Generate the list of start and end dates for each month
dates = []
current_date = start_date
while current_date <= end_date:
    start_month_date = current_date
    end_month_date = (start_month_date + relativedelta(months=3)) - timedelta(days=1)

    # Ensure the end_month_date does not exceed the end_date
    if end_month_date > end_date:
        end_month_date = end_date

    dates.append([start_month_date.strftime('%Y-%m-%d'), end_month_date.strftime('%Y-%m-%d')])
    current_date += relativedelta(months=3)

# Create a DataFrame
date_range_df = pd.DataFrame(dates, columns=['Start_Date', 'End_Date'])

In [12]:
#Define which quartal
start = date_range_df['Start_Date'][1]
end = date_range_df['End_Date'][1]

## Final map for selected sitecode and quartal

### Test

In [28]:
#Start and end of specific quartal
START = ee.Date(start)
END = ee.Date(end)

# Create a filter based on the geometry of the shapefile/protected area and on quartal
specific_feature_collection = shapefile.filter(ee.Filter.eq('SITECODE', pa_sitecode))

geometry = specific_feature_collection.geometry()

col_filter = ee.Filter.And(
    ee.Filter.geometry(geometry),
    ee.Filter.date(START, END),
)

# Apply the filter to the DynamicWorld collection
dw_col = ee.ImageCollection('GOOGLE/DYNAMICWORLD/V1').filter(col_filter).filterBounds(geometry)
dw_col_clipped = dw_col.map(lambda image: image.clip(geometry))
s2_col = ee.ImageCollection('COPERNICUS/S2').filter(col_filter)


# Join corresponding DW and S2 images (by system:index).
dw_s2_col = ee.Join.saveFirst('s2_img').apply(
    dw_col_clipped,
    s2_col,
    ee.Filter.equals(leftField='system:index', rightField='system:index'),
)

# Extract an example DW image and its source S2 image.
dw_image = ee.Image(dw_s2_col.first())
s2_image = ee.Image(dw_image.get('s2_img'))

# List of landcovers
CLASS_NAMES = [
    'water',
    'trees',
    'grass',
    'flooded_vegetation',
    'crops',
    'shrub_and_scrub',
    'built',
    'bare',
    'snow_and_ice',
]

#Color palette of each landcover
VIS_PALETTE = [
    '419bdf',
    '397d49',
    '88b053',
    '7a87c6',
    'e49635',
    'dfc35a',
    'c4281b',
    'a59b8f',
    'b39fe1',
]

# Create an RGB image of the label (most likely class) on [0, 1].
dw_rgb = (
    dw_image.select('label')
    .visualize(min=0, max=8, palette=VIS_PALETTE)
    .divide(255)
)

# Get the most likely class probability.
top1_prob = dw_image.select(CLASS_NAMES).reduce(ee.Reducer.max())

# Create a hillshade of the most likely class probability on [0, 1]
top1_prob_hillshade = ee.Terrain.hillshade(top1_prob.multiply(100)).divide(255)

# Combine the RGB image with the hillshade.
dw_rgb_hillshade = dw_rgb.multiply(top1_prob_hillshade)

#Get lon and lat of protected area
dict_pa = specific_feature_collection.getInfo()
lon = dict_pa.get('features')[0].get('properties').get('lon')
lat = dict_pa.get('features')[0].get('properties').get('lat')

#Initialise map
m = geemap.Map()
#Set map center on lon and lat of protected areas / zoom:13
m.set_center(lon, lat, 13)

#Add dynamic world layer
m.add_layer(
    dw_rgb_hillshade,
    {'min': 0, 'max': 0.65},
    'Dynamic World V1 - label hillshade',
)

#Add protected area layer
m.add_layer(
    geometry
)

#display map
m

/Users/amelietatin/.pyenv/versions/3.10.6/envs/Predicting_land_cover/lib/python3.10/site-packages/ee/deprecation.py:204: DeprecationWarning: 

Attention required for COPERNICUS/S2! You are using a deprecated asset.
To ensure continued functionality, please update it.
Learn more: https://developers.google.com/earth-engine/datasets/catalog/COPERNICUS_S2

  warnings.warn(warning, category=DeprecationWarning)


Map(center=[42.497396362345434, 27.392258798599347], controls=(WidgetControl(options=['position', 'transparent…

### Try

In [15]:
start

'2015-10-01'

In [37]:
#Start and end of specific quartal
START = ee.Date(start)
END = ee.Date(end)

# Create a filter based on the geometry of the shapefile/protected area and on quartal
specific_feature_collection = shapefile.filter(ee.Filter.eq('SITECODE', pa_sitecode))

geometry = specific_feature_collection.geometry()

col_filter = ee.Filter.And(
    ee.Filter.geometry(geometry),
    ee.Filter.date(START, END),
)

# Apply the filter to the DynamicWorld collection
dw_col = ee.ImageCollection('GOOGLE/DYNAMICWORLD/V1').filter(col_filter).filterBounds(geometry)
dw_col_clipped = dw_col.map(lambda image: image.clip(geometry))
s2_col = ee.ImageCollection('COPERNICUS/S2').filter(col_filter)


# Join corresponding DW and S2 images (by system:index).
dw_s2_col = ee.Join.saveFirst('s2_img').apply(
    dw_col_clipped,
    s2_col,
    ee.Filter.equals(leftField='system:index', rightField='system:index'),
)

# Extract an example DW image and its source S2 image.
dw_image = ee.Image(dw_s2_col.first())
s2_image = ee.Image(dw_image.get('s2_img'))

# List of landcovers
CLASS_NAMES = [
    'water',
    'trees',
    'grass',
    'flooded_vegetation',
    'crops',
    'shrub_and_scrub',
    'built',
    'bare',
    'snow_and_ice',
]

#Color palette of each landcover
VIS_PALETTE = [
    '419bdf',
    '397d49',
    '88b053',
    '7a87c6',
    'e49635',
    'dfc35a',
    'c4281b',
    'a59b8f',
    'b39fe1',
]

# Create an RGB image of the label (most likely class) on [0, 1].
dw_rgb = (
    dw_image.select('label')
    .visualize(min=0, max=8, palette=VIS_PALETTE)
    .divide(255)
)

# Get the most likely class probability.
top1_prob = dw_image.select(CLASS_NAMES).reduce(ee.Reducer.max())

# Create a hillshade of the most likely class probability on [0, 1]
top1_prob_hillshade = ee.Terrain.hillshade(top1_prob.multiply(100)).divide(255)

# Combine the RGB image with the hillshade.
dw_rgb_hillshade = dw_rgb.multiply(top1_prob_hillshade)

#Get lon and lat of protected area
dict_pa = specific_feature_collection.getInfo()
lon = dict_pa.get('features')[0].get('properties').get('lon')
lat = dict_pa.get('features')[0].get('properties').get('lat')

#GEEMAP##################
#Initialise map
m = geemap.Map()
#Set map center on lon and lat of protected areas / zoom:13
m.set_center(lon, lat, 13)

#Add dynamic world layer
m.add_layer(
    dw_rgb_hillshade,
    {'min': 0, 'max': 0.65},
    'Dynamic World V1 - label hillshade',
)

#Add protected area layer
m.add_layer(
    geometry
)

#IPYLEAFLET##################


#display map
m

Map(center=[42.497396362345434, 27.392258798599347], controls=(WidgetControl(options=['position', 'transparent…

In [63]:
!pip freeze | grep geemap

geemap==0.17.2


In [62]:
!pip freeze | grep ipyleaflet

ipyleaflet==0.16.0


In [65]:
#!pip install --upgrade geemap

  Using cached geemap-0.32.1-py2.py3-none-any.whl.metadata (14 kB)
  Using cached ipyleaflet-0.18.2-py3-none-any.whl.metadata (1.0 kB)


Using cached geemap-0.32.1-py2.py3-none-any.whl (2.2 MB)
Using cached ipyleaflet-0.18.2-py3-none-any.whl (3.7 MB)
  Attempting uninstall: ipyleaflet
    Found existing installation: ipyleaflet 0.16.0
    Uninstalling ipyleaflet-0.16.0:
      Successfully uninstalled ipyleaflet-0.16.0


  Attempting uninstall: geemap
    Found existing installation: geemap 0.17.2
    Uninstalling geemap-0.17.2:
      Successfully uninstalled geemap-0.17.2


In [61]:
#!pip install ipyleaflet

In [58]:
#!pip install geemap==0.17.2

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.7/224.7 kB 4.3 MB/s eta 0:00:00a 0:00:01
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing metadata (pyproject.toml) ... done


  Using cached tqdm-4.66.4-py3-none-any.whl.metadata (57 kB)


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 6.4 MB/s eta 0:00:0000:0100:01m
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 108.6/108.6 kB 10.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 22.0 MB/s eta 0:00:00a 0:00:01
Using cached tqdm-4.66.4-py3-none-any.whl (78 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 72.3/72.3 kB 7.2 MB/s eta 0:00:00
  Created wheel for ee-extra: filename=ee_extra-0.0.15-py3-none-any.whl size=236755 sha256=a9150eeefd27c736f490ee26acc40b5bb3642a01c5be743ed70802bb48ce0d8a
  Stored in directory: /Users/amelietatin/Library/Caches/pip/wheels/29/96/0e/4e36b0dfd85e16867723df739294c0aa45a65b191adac4d959
  Created wheel for pycrs: filename=PyCRS-1.0.2-py3-none-any.whl size=32687 sha256=ea292be483c8c1c0cadc07f58c501fd9ad8ff3178aabadfe498569f6221922e8
  Stored in directory: /Users/amelietatin/Library/Caches/pip/wheels/47/1d/70/7a5bdf33347e7c75e95b06b1fa38f076a59a9506653cc24aff
Successfully built ee-extra pycrs
  Attempting uninstall: 